In [4]:
import pandas as pd
import numpy as np
import time
import json
import pickle
from tqdm.auto import tqdm
from typing import List, Dict, Tuple

In [5]:
# Read Telugu books data
books_df = pd.read_csv('./archive/telugu_books/telugu_books.csv')

# Display basic information about the datasets
print("\nDataset Information:")
print("\nBooks Dataset Shape:", books_df.shape)


Dataset Information:

Books Dataset Shape: (25793, 2)


In [6]:
print("Telugu Books Dataset:")
books_df.head(5)

Telugu Books Dataset:


SNo                                               text
0    0  \r\n    సుశీలమ్మ కళ్ళలో భయం పారాడింది.\r\n    ...
1    1                                                ...
2    2      "ఎలా వుంది ఫ్రెండ్..... "\n\r\n    "టప్ టప...
3    3      "అది ఊరుకున్నా  మీరు వుండలేరు. మీరిద్దరే  ...
4    4      అయన అలా వెళ్ళిపోగానే గుమ్మం పక్కనుంచి  రాజ...

In [8]:
# Get just the text columns
books_text = books_df['text'].values

# Combine all texts into one list
all_texts = np.concatenate([books_text])

# Remove any None or NaN values
all_texts = [text for text in all_texts if isinstance(text, str)]

In [9]:
all_texts

['\r\n\xa0\xa0 \xa0సుశీలమ్మ కళ్ళలో భయం పారాడింది.\r\n\xa0\xa0 \xa0"అనాధ బిడ్డ అని చిన్నప్పుడే తెలిస్తే మన దగ్గిరవాడు అలా అరమరిక లేకుండా చనువుగా పెరిగేవాడా?" పుట్టెడు దిగులు సుశీలమ్మ కంఠంలో పలికింది.\r\n\xa0\xa0 \xa0"అది మనం పెంచేదాన్ని బట్టి వుంటుంది. అటువంటి బేధాలు మనలో లేనట్టు తెలుసుకొనేలా పెంచాలి."\r\n\xa0\xa0 \xa0"చాలామంది అలాగే పెంచుతారు గదండీ."\r\n\xa0\xa0 \xa0"ఏనాడో ఒకనాడు ఆ విషయం తెలియకపోదు. మనం పట్నంలో వుంటున్నాం గనక యింత కాలమయినా ఈ రహస్యాన్ని దాచగలిగాం.\r\n\xa0\xa0 \xa0సుశీలమ్మ వింటూ కూర్చుంది.\r\n\xa0\xa0 \xa0"ఒక వ్యక్తిత్వం అంటూ ఏర్పడ్డాక ఆ రహస్యం తెలిస్తే లోతుగా గాయపడతారు. అనేక ఆలోచనలు వస్తాయి. చిన్నప్పుడే తెలిస్తే అంతగా తలక్రిందులై పోరు" అన్నాడు. \xa0\r\n\xa0\xa0 \xa0"వాడు మనల్ని వదిలేసి వెళ్ళిపోతాడేమో!" అనలేక అంటున్న ఆమె గొంతులో ఏదో అడ్డుపడినట్టు ఉక్కిరిబిక్కిరి అయిపోతుంది.\r\n\xa0\xa0 \xa0రామనాథానికి కూడా ఆ భయం లేకపోలేదు.\r\n\xa0\xa0 \xa0ఆ భయాన్ని దాచుకుంటూ వెళ్ళడు. ఎలా వెళతాడు? ఎక్కడికి వెళతాడు? అసలు ఎందుకు వెళ్ళాలి? వాడికి మనమేం తక్కువ చేశామని వెళ్తాడు?" అన్నాడు.\r\n\

In [10]:
len(all_texts)

25774

In [11]:
import string
print(string.punctuation)

!"#$%&'()*+,-./:;<=>?@[\]^_`{|}~


In [12]:
# Clean the texts by removing special characters and extra whitespace
def clean_text(text):
    # Remove special characters and extra whitespace
    text = text.replace('\r', ' ')
    text = text.replace('\n', ' ')
    text = text.replace('\xa0', ' ')
    
    # Remove all punctuation using string.punctuation
    for punct in string.punctuation:
        text = text.replace(punct, ' ')

    # Remove all digits using string.digits
    for digit in string.digits:
        text = text.replace(digit, ' ')
    
    # Replace multiple spaces with single space
    text = ' '.join(text.split())
    return text

# Clean all texts
all_texts_cleaned = [clean_text(text) for text in all_texts]

In [31]:
all_texts_cleaned[1000]

'అది మీకు కొత్తగాదు నాకెవరూ దాన్ని నేర్పక్కర్లేదను కుంటాను ఏ కమిటీ మెంబర్ సూక్ష్మ పరీక్షకయినా మరో కమిటీ మెంబర్ అడ్డు రాకూడదు అది విశ్వాత్మ వీలునామాలో స్పష్టంగా వుంది అసహనంగా తన సీట్లో కదులుతూ కూర్చున్నాడు ధృతకుమార్ వారిమధ్య జరుగుతున్న వాగ్వివాదాన్ని ఆనందంగా తిలకిస్తోంది శృతి ఒకసారి తప్పుచేస్తే పొరపాటు రెండోసారి చేస్తే గ్రహపాటు మూడోసారి చేస్తే అది చెడ్డ అలవాటు మనమిప్పుడు ఇక్కడ సమావేశమయింది పొరపాటు చేయటానికి గ్రహపాటుకి లోనుకావటానికి కాదు మిస్టర్ మిత్రా నాకన్నా వయస్సులో చిన్నవాడివి ఆ చనువుతోనే చెబుతున్నాను తొందరపాటు మంచిది కాదు ఇక్కడ మనమందరం కలిసి విశ్వాత్మనంటూ వచ్చిన వ్యక్తిని శల్యపరీక్ష చేయాలేగాని మనల్ని మనంకాదు యజ్ఞవల్కి సౌమ్యంగానే అన్నా ఆయన మాటల్లో ఒకింత కరుకుదనం తొంగిచూడక పోలేదు మిత్రా మౌనంగా వున్నా లోలోన కుతకుతలాడిపోయాడు నీలో నువ్వు అవధులు కల్పించుకుని విడి ముక్కలై పోయి విభాగమయిన నీ ఆత్మని లక్షపేర్లతో పిలుచుకుంటే ఆ స్వయంకల్పిత విభజన నేను గా రూపొందుతుంది నాయనా అదే అహానికి దారితీస్తుంది అహం అంచునే వినాశనం పొంచి వుంటుంది చిరంజీవి ధృతకుమార్ అన్న మాటల్లో నాకు తప్పేమీ కనిపించలేదు అతడ్ని స

In [30]:
with open('telugu_preprocessed_file.txt', 'w', encoding='utf-8') as f:
    for text in all_texts_cleaned[1000]:  # assuming your text is in a list called 'texts'
        f.write(text + '\n')

In [32]:
tokens = []
for text in all_texts_cleaned[1000]:
    bytes_tokens = text.encode('utf-8')
    tokens.extend(list(map(int, bytes_tokens)))

# print(tokens)
print(len(tokens))

12326


In [17]:
max(tokens)

224

In [ ]:
# example
# p_count = {}
# ids = tokens[:50]
# print(ids)
# for pair in zip(ids, ids[1:]):
#     p_count[pair] = p_count.get(pair, 0) + 1
# p_count

In [19]:
most_repeated_pair = max(stats, key=stats.get)
most_repeated_pair



(224, 176)

In [20]:
len(stats)

129

In [21]:
def merge(ids, pair, idx):
  newids = []
  i = 0
  while i < len(ids):
    if i < len(ids) - 1 and ids[i] == pair[0] and ids[i+1] == pair[1]:
      newids.append(idx)
      i += 2
    else:
      newids.append(ids[i])
      i += 1
  return newids

  

In [24]:
# Train BPE up to vocab_size 350
vocab_size = 350  # 256 + 94 merges
num_merges = vocab_size - 256
ids = list(tokens)  # Start with original tokens

merges = {}
for i in range(num_merges):
    stats = get_stats(ids)
    pair = max(stats, key=stats.get)
    idx = 256 + i
    print(f"merging {pair} into a new token {idx}")
    ids = merge(ids, pair, idx)
    merges[pair] = idx

# Calculate compression stats
print("\nCompression Statistics:")
print("Original tokens length:", len(tokens))
print("Compressed ids length:", len(ids))
print(f"Compression ratio: {len(tokens) / len(ids):.2f}X")

merging (224, 176) into a new token 256
merging (224, 177) into a new token 257
merging (32, 256) into a new token 258
merging (256, 191) into a new token 259
merging (257, 141) into a new token 260
merging (260, 256) into a new token 261
merging (257, 129) into a new token 262
merging (256, 190) into a new token 263
merging (259, 256) into a new token 264
merging (263, 256) into a new token 265
merging (130, 256) into a new token 266
merging (262, 256) into a new token 267
merging (259, 258) into a new token 268
merging (257, 139) into a new token 269
merging (256, 168) into a new token 270
merging (262, 258) into a new token 271
merging (256, 266) into a new token 272
merging (257, 135) into a new token 273
merging (256, 176) into a new token 274
merging (256, 149) into a new token 275
merging (256, 178) into a new token 276
merging (256, 164) into a new token 277
merging (261, 168) into a new token 278
merging (256, 184) into a new token 279
merging (269, 258) into a new token 280
m

In [25]:
tokens[:1]

[224]

In [26]:

class OptimizedBPETokenizer:
    def __init__(self, merges: Dict[Tuple[int, int], int]):
        self.merges = merges
        self.idx_to_pair = {idx: pair for pair, idx in merges.items()}
        
        # Create lookup table for faster encoding
        self.merge_lookup = {}
        for (first, second), idx in merges.items():
            if first not in self.merge_lookup:
                self.merge_lookup[first] = {}
            self.merge_lookup[first][second] = idx
    
    def encode(self, text: str, chunk_size: int = 1000000) -> List[int]:
        if not isinstance(text, str):
            return []
        
        # Convert to numpy array for faster processing
        ids = np.array(list(text.encode('utf-8')), dtype=np.uint16)
        
        # Process in chunks to handle large texts
        result = []
        for i in range(0, len(ids), chunk_size):
            chunk = ids[i:i + chunk_size]
            processed_chunk = self._encode_chunk(chunk)
            result.extend(processed_chunk)
            
        return result
    
    def _encode_chunk(self, ids: np.ndarray) -> List[int]:
        output = []
        i = 0
        while i < len(ids):
            if i < len(ids) - 1:
                first, second = ids[i], ids[i + 1]
                if first in self.merge_lookup and second in self.merge_lookup[first]:
                    output.append(self.merge_lookup[first][second])
                    i += 2
                    continue
            output.append(ids[i])
            i += 1
        return output
    
    def decode(self, ids: List[int], chunk_size: int = 1000000) -> str:
        # Process in chunks
        byte_tokens = []
        for i in range(0, len(ids), chunk_size):
            chunk = ids[i:i + chunk_size]
            decoded_chunk = self._decode_chunk(chunk)
            byte_tokens.extend(decoded_chunk)
            
        return bytes(byte_tokens).decode('utf-8')
    
    def _decode_chunk(self, ids: List[int]) -> List[int]:
        result = []
        for token in ids:
            if token < 256:
                result.append(token)
            else:
                result.extend(self._expand_token(token))
        return result
    
    def _expand_token(self, token: int) -> List[int]:
        if token < 256:
            return [token]
            
        pair = self.idx_to_pair[token]
        expanded = []
        for t in pair:
            expanded.extend(self._expand_token(t))
        return expanded


In [27]:
tokenizer = OptimizedBPETokenizer(merges)

# Test with a larger text
# test_text = "నమస్కారం" 

test_text = """వికీపీడియా ఎవరైనా రాయదగిన స్వేచ్ఛా విజ్ఞాన సర్వస్వము.
ఇక్కడ సమాచారాన్ని వాడుకోవటమే కాదు, ఉన్న సమాచారంలో అవసరమైన మార్పుచేర్పులు చెయ్యవచ్చు, కొత్త సమాచారాన్ని చేర్చవచ్చు.
ప్రస్తుతం తెలుగు వికీపీడియాలో 1,02,552 వ్యాసాలున్నాయి. పూర్తి గణాంకాలు చూడండి."""  # Repeat text for better testing

# Encode and show results
start = time.time()
encoded = tokenizer.encode(test_text)
encode_time = time.time() - start
print(f"Encoding time: {encode_time:.3f}s")

# Show sample of encoded tokens
print("\nEncoded tokens (first 20):")
print(encoded)
print(f"Total encoded length: {len(encoded)}")

# Decode and show results
start = time.time()
decoded = tokenizer.decode(encoded)
decode_time = time.time() - start
print(f"\nDecoding time: {decode_time:.3f}s")

# Show sample of decoded text
print("\nOriginal text (first 50 chars):")
print(test_text)
print("\nDecoded text (first 50 chars):")
print(decoded)

# Show any differences if they exist
if test_text != decoded:
    print("\nFirst difference occurs at position:", end=" ")
    for i, (orig, dec) in enumerate(zip(test_text, decoded)):
        if orig != dec:
            print(f"{i}, Original: '{orig}', Decoded: '{dec}'")
            break
else:
    print("\nTexts match perfectly!")

Encoding time: 0.000s

Encoded tokens (first 20):
[256, 181, 256, 191, 256, 149, 257, 128, 256, 170, 257, 128, 256, 161, 256, 191, 256, 175, 256, 190, 32, 256, 142, 256, 181, 256, 176, 257, 136, 256, 168, 256, 190, 32, 256, 176, 256, 190, 256, 175, 256, 166, 256, 151, 256, 191, 256, 168, 32, 256, 184, 257, 141, 256, 181, 257, 135, 256, 154, 257, 141, 256, 155, 256, 190, 32, 256, 181, 256, 191, 256, 156, 257, 141, 256, 158, 256, 190, 256, 168, 32, 256, 184, 256, 176, 257, 141, 256, 181, 256, 184, 257, 141, 256, 181, 256, 174, 257, 129, 46, 10, 256, 135, 256, 149, 257, 141, 256, 149, 256, 161, 32, 256, 184, 256, 174, 256, 190, 256, 154, 256, 190, 256, 176, 256, 190, 256, 168, 257, 141, 256, 168, 256, 191, 32, 256, 181, 256, 190, 256, 161, 257, 129, 256, 149, 257, 139, 256, 181, 256, 159, 256, 174, 257, 135, 32, 256, 149, 256, 190, 256, 166, 257, 129, 44, 32, 256, 137, 256, 168, 257, 141, 256, 168, 32, 256, 184, 256, 174, 256, 190, 256, 154, 256, 190, 256, 176, 256, 130, 256, 178, 257, 13

In [28]:
# with open("bpe_vocab_350_merges.pkl", "wb") as f:
#     pickle.dump(merges, f)